# Playing Differentiated Demand Environemnt

In [8]:
#Imports

from marketsai.markets.diff_demand import DiffDemand

#import ray

from ray import tune, shutdown, init
from ray.tune.registry import register_env
from ray.rllib.agents.a3c.a2c import A2CTrainer
from ray.rllib.agents.dqn.dqn import DQNTrainer
from ray.tune.integration.mlflow import MLflowLoggerCallback
from ray.rllib.utils.exploration.epsilon_greedy import EpsilonGreedy
from ray.rllib.utils.schedules.exponential_schedule import ExponentialSchedule

import random
import math
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import logging

In [9]:
# STEP 0: Inititialize ray
NUM_CPUS = 9
shutdown()
init(num_cpus=NUM_CPUS, 
    logging_level=logging.ERROR,
)

{'node_ip_address': '192.168.1.202',
 'raylet_ip_address': '192.168.1.202',
 'redis_address': '192.168.1.202:6379',
 'object_store_address': '/tmp/ray/session_2021-04-12_13-05-05_604932_19427/sockets/plasma_store',
 'raylet_socket_name': '/tmp/ray/session_2021-04-12_13-05-05_604932_19427/sockets/raylet',
 'webui_url': '127.0.0.1:8266',
 'session_dir': '/tmp/ray/session_2021-04-12_13-05-05_604932_19427',
 'metrics_export_port': 59320,
 'node_id': '07cf9e3eb4b811bf9b080e0de71da3c053e3e86d76dd16367ae9ff62'}

In [10]:
# STEP 1: register environment
register_env("diffdemand", DiffDemand)
env = DiffDemand()
policy_ids = [f"policy_{i}" for i in range(env.n_agents)]

In [11]:
# STEP 2: Experiment configuration

MAX_STEPS = 3000 * 1000
PRICE_BAND_WIDE = 0.1
LOWER_PRICE = 1.47 - PRICE_BAND_WIDE
HIGHER_PRICE = 1.93 + PRICE_BAND_WIDE
DEC_RATE = float(math.e ** (-4 * 10 ** (-6)))
DEC_RATE_HIGH = float(math.e ** (-4 * 10 ** (-6) * 4))

env_config = {
    "mkt_config": {
    "lower_price": [LOWER_PRICE for i in range(env.n_agents)],
    "higher_price": [HIGHER_PRICE for i in range(env.n_agents)],
    "parameteres": {
                "cost": [1 for i in range(env.n_agents)],
                "values": [2 for i in range(env.n_agents)],
                "ext_demand": 0,
                "substitution": 0.25,
    },
    "space_type": "MultiDiscrete",
    "gridpoints": 16,
    }
}


exploration_config = {"type": "EpsilonGreedy",
    "epsilon_schedule": ExponentialSchedule(
      schedule_timesteps = int(1),
      framework="Torch",
      initial_p=float(1.0),
      decay_rate=float(DEC_RATE),
    ),
}

training_config = {
    "gamma": 0.95,
    "lr": 0.15,
    "env": "diffdemand",
    "exploration_config": exploration_config,
    "env_config": env_config,
    "horizon": 100,
    "soft_horizon": True,
    "no_done_at_end": True,
    "multiagent": {
        "policies": {
            policy_ids[i]: (
                None,
                env.observation_space["agent_{}".format(i)],
                env.action_space["agent_{}".format(i)],
                {},
            )
            for i in range(env.n_agents)
        },
        "policy_mapping_fn": (lambda agent_id: policy_ids[int(agent_id.split("_")[1])]),
    },
    "framework": "torch",
    "num_workers": NUM_CPUS - 1,
    "num_gpus": 0,
    "timesteps_per_iteration": 1000,
}

stop = {"training_iteration": MAX_STEPS/1000}

In [12]:
#Step 3: Experiments

exp_name = "DQN_test_April9"
results = tune.run(
    "DQN",
    name=exp_name,
    config=training_config,
    #checkpoint_freq=250,
    checkpoint_at_end=True,
    stop=stop,
    metric="episode_reward_mean",
    mode="max",
    callbacks=[MLflowLoggerCallback(experiment_name=exp_name, save_artifact=True)],
    verbose=3
)

best_checkpoint_DQN = results.best_checkpoint
print("Best checkpont:", best_checkpoint_DQN)

 been deprecated. Use `num_framestacks (int)` instead. This will raise an error in the future!
(pid=21200) 2021-04-12 13:05:12,814	WARNING deprecation.py:33 -- DeprecationWarning: `framestack` has been deprecated. Use `num_framestacks (int)` instead. This will raise an error in the future!
(pid=21201) 2021-04-12 13:05:12,856	WARNING deprecation.py:33 -- DeprecationWarning: `framestack` has been deprecated. Use `num_framestacks (int)` instead. This will raise an error in the future!
(pid=21201) 2021-04-12 13:05:12,861	WARNING deprecation.py:33 -- DeprecationWarning: `framestack` has been deprecated. Use `num_framestacks (int)` instead. This will raise an error in the future!
(pid=21201) 2021-04-12 13:05:12,856	WARNING deprecation.py:33 -- DeprecationWarning: `framestack` has been deprecated. Use `num_framestacks (int)` instead. This will raise an error in the future!
(pid=21201) 2021-04-12 13:05:12,861	WARNING deprecation.py:33 -- DeprecationWarning: `framestack` has been deprecated. Us

Result for DQN_diffdemand_3b8c4_00000:
  custom_metrics: {}
  date: 2021-04-12_13-05-20
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 56.17082453405669
  episode_reward_mean: 53.943379492880304
  episode_reward_min: 51.752128146270366
  episodes_this_iter: 8
  episodes_total: 48
  experiment_id: 2ddaa5d363c444cf9f43042b9151c47f
  hostname: Matiass-MacBook-Pro.local
  info:
    last_target_update_ts: 5120
    learner:
      policy_0:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 16.35887336730957
        max_q: 41.77446746826172
        mean_q: 40.79328155517578
        mean_td_error: 1.3590792417526245
        min_q: 39.8621711730957
      policy_1:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 14.293238639831543
        max_q: 53.321693420410156
        mean_q: 52.71045684814453
        mean_td_error: 1.1758366823196411
        min_q: 51.89693832397461
    num_steps_sampled: 5120
    num_steps_trained: 4128
    num_ta

Result for DQN_diffdemand_3b8c4_00000:
  custom_metrics: {}
  date: 2021-04-12_13-05-27
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 56.17082453405669
  episode_reward_mean: 53.992152705023166
  episode_reward_min: 51.52952069043702
  episodes_this_iter: 8
  episodes_total: 88
  experiment_id: 2ddaa5d363c444cf9f43042b9151c47f
  hostname: Matiass-MacBook-Pro.local
  info:
    last_target_update_ts: 9216
    learner:
      policy_0:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 13.688346862792969
        max_q: 34.445037841796875
        mean_q: 34.00699234008789
        mean_td_error: -1.2947319746017456
        min_q: 33.341636657714844
      policy_1:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 14.080678939819336
        max_q: 43.24806594848633
        mean_q: 42.11859893798828
        mean_td_error: 1.7403194904327393
        min_q: 39.99506759643555
    num_steps_sampled: 9216
    num_steps_trained: 8224
    num

Result for DQN_diffdemand_3b8c4_00000:
  custom_metrics: {}
  date: 2021-04-12_13-05-33
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 56.17082453405669
  episode_reward_mean: 53.97798606546476
  episode_reward_min: 51.52952069043702
  episodes_this_iter: 8
  episodes_total: 128
  experiment_id: 2ddaa5d363c444cf9f43042b9151c47f
  hostname: Matiass-MacBook-Pro.local
  info:
    last_target_update_ts: 13312
    learner:
      policy_0:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 1.2917709350585938
        max_q: 30.514339447021484
        mean_q: 30.235212326049805
        mean_td_error: -0.10063982009887695
        min_q: 29.918378829956055
      policy_1:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 11.18481159210205
        max_q: 41.224220275878906
        mean_q: 40.507938385009766
        mean_td_error: 1.109839677810669
        min_q: 39.25877380371094
    num_steps_sampled: 13312
    num_steps_trained: 12320
  

Result for DQN_diffdemand_3b8c4_00000:
  custom_metrics: {}
  date: 2021-04-12_13-05-39
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 56.29587240220278
  episode_reward_mean: 54.04637064506474
  episode_reward_min: 51.55336103433865
  episodes_this_iter: 8
  episodes_total: 168
  experiment_id: 2ddaa5d363c444cf9f43042b9151c47f
  hostname: Matiass-MacBook-Pro.local
  info:
    last_target_update_ts: 17408
    learner:
      policy_0:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.14043332636356354
        max_q: 23.766019821166992
        mean_q: 23.489858627319336
        mean_td_error: 0.040197789669036865
        min_q: 23.3374080657959
      policy_1:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 9.448989868164062
        max_q: 32.16331100463867
        mean_q: 31.75145721435547
        mean_td_error: -0.9414322972297668
        min_q: 30.825101852416992
    num_steps_sampled: 17408
    num_steps_trained: 16416
  

...

Result for DQN_diffdemand_3b8c4_00000:
  custom_metrics: {}
  date: 2021-04-12_15-03-15
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 57.41186127206987
  episode_reward_mean: 52.96249298872886
  episode_reward_min: 46.20209731234815
  episodes_this_iter: 8
  episodes_total: 30624
  experiment_id: 2ddaa5d363c444cf9f43042b9151c47f
  hostname: Matiass-MacBook-Pro.local
  info:
    last_target_update_ts: 3062784
    learner:
      policy_0:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.004431153181940317
        max_q: 3.839207649230957
        mean_q: 3.684866189956665
        mean_td_error: -0.04481832683086395
        min_q: 3.5730714797973633
      policy_1:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.017512589693069458
        max_q: 2.459850311279297
        mean_q: 2.2547221183776855
        mean_td_error: -0.19226154685020447
        min_q: 2.090723991394043
    num_steps_sampled: 3062784
    num_steps_traine

Result for DQN_diffdemand_3b8c4_00000:
  custom_metrics: {}
  date: 2021-04-12_15-03-22
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 58.08415547850453
  episode_reward_mean: 53.33926518175187
  episode_reward_min: 46.20209731234815
  episodes_this_iter: 8
  episodes_total: 30656
  experiment_id: 2ddaa5d363c444cf9f43042b9151c47f
  hostname: Matiass-MacBook-Pro.local
  info:
    last_target_update_ts: 3065856
    learner:
      policy_0:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.005002638325095177
        max_q: 3.8768653869628906
        mean_q: 3.796351909637451
        mean_td_error: -0.05090460926294327
        min_q: 3.706597089767456
      policy_1:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.017124060541391373
        max_q: 2.513366937637329
        mean_q: 2.401538610458374
        mean_td_error: -0.1779738962650299
        min_q: 2.259510040283203
    num_steps_sampled: 3065856
    num_steps_trained:

Result for DQN_diffdemand_3b8c4_00000:
  custom_metrics: {}
  date: 2021-04-12_15-03-27
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 58.08415547850453
  episode_reward_mean: 53.09838807201102
  episode_reward_min: 46.20209731234815
  episodes_this_iter: 16
  episodes_total: 30688
  experiment_id: 2ddaa5d363c444cf9f43042b9151c47f
  hostname: Matiass-MacBook-Pro.local
  info:
    last_target_update_ts: 3068928
    learner:
      policy_0:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.01667851395905018
        max_q: 4.12650728225708
        mean_q: 3.9022481441497803
        mean_td_error: -0.1808125376701355
        min_q: 3.6650187969207764
      policy_1:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.0074919648468494415
        max_q: 2.8321571350097656
        mean_q: 2.682713031768799
        mean_td_error: -0.08862030506134033
        min_q: 2.5937345027923584
    num_steps_sampled: 3068928
    num_steps_train

Result for DQN_diffdemand_3b8c4_00000:
  custom_metrics: {}
  date: 2021-04-12_15-03-34
  done: true
  episode_len_mean: 100.0
  episode_reward_max: 58.08415547850453
  episode_reward_mean: 53.19942952996097
  episode_reward_min: 48.27968720028034
  episodes_this_iter: 16
  episodes_total: 30720
  experiment_id: 2ddaa5d363c444cf9f43042b9151c47f
  hostname: Matiass-MacBook-Pro.local
  info:
    last_target_update_ts: 3072000
    learner:
      policy_0:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.04083648696541786
        max_q: 3.4761900901794434
        mean_q: 3.3554346561431885
        mean_td_error: -0.47810208797454834
        min_q: 3.1348912715911865
      policy_1:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.002265761373564601
        max_q: 3.408682107925415
        mean_q: 3.302133083343506
        mean_td_error: -0.023767247796058655
        min_q: 3.202605962753296
    num_steps_sampled: 3072000
    num_steps_train

Best checkpont: /Users/matiascovarrubias/ray_results/DQN_test_April9/DQN_diffdemand_3b8c4_00000_0_2021-04-12_13-05-07/checkpoint_3000/checkpoint-3000


## Continuous Space


In [13]:
#DDGP uses its own exploration config
# See exploration config in https://github.com/ray-project/ray/blob/master/rllib/utils/exploration/ornstein_uhlenbeck_noise.pyDDPG 
exploration_config = {
        # DDPG uses OrnsteinUhlenbeck (stateful) noise to be added to NN-output
        # actions (after a possible pure random phase of n timesteps).
        "type": "OrnsteinUhlenbeckNoise",
        "final_scale": 0.02,
        "scale_timesteps": 100000,
    }

training_config["exploration_config"] = exploration_config
env_config["mkt_config"]["space_type"] = "Continuous"

env=DiffDemand(env_config)
training_config["env_config"] = env_config
training_config["multiagent"]["policies"] =  {
            policy_ids[i]: (None, env.observation_space[f"agent_{i}"], env.action_space[f"agent_{i}"],{},) for i in range(env.n_agents)
}
#print(env_config)
print(training_config)
print(env.action_space)


{'gamma': 0.95, 'lr': 0.15, 'env': 'diffdemand', 'exploration_config': {'type': 'OrnsteinUhlenbeckNoise', 'final_scale': 0.02, 'scale_timesteps': 100000}, 'env_config': {'mkt_config': {'lower_price': [1.3699999999999999, 1.3699999999999999], 'higher_price': [2.03, 2.03], 'parameteres': {'cost': [1, 1], 'values': [2, 2], 'ext_demand': 0, 'substitution': 0.25}, 'space_type': 'Continuous', 'gridpoints': 16}}, 'horizon': 100, 'soft_horizon': True, 'no_done_at_end': True, 'multiagent': {'policies': {'policy_0': (None, Box(1.3699999999999999, 2.03, (2,), float64), Box(1.3699999999999999, 2.03, (1,), float64), {}), 'policy_1': (None, Box(1.3699999999999999, 2.03, (2,), float64), Box(1.3699999999999999, 2.03, (1,), float64), {})}, 'policy_mapping_fn': <function <lambda> at 0x346583550>}, 'framework': 'torch', 'num_workers': 8, 'num_gpus': 0, 'timesteps_per_iteration': 1000}
{'agent_0': Box(1.3699999999999999, 2.03, (1,), float64), 'agent_1': Box(1.3699999999999999, 2.03, (1,), float64)}


In [14]:
exp_name = "DDPG_cont_test_April9"
results = tune.run(
    "DDPG",
    name=exp_name,
    config=training_config,
    #checkpoint_freq=250,
    checkpoint_at_end=True,
    stop=stop,
    metric="episode_reward_mean",
    mode="max",
    callbacks=[MLflowLoggerCallback(experiment_name=exp_name, save_artifact=True)],
    verbose=3
)

best_checkpoint_DDPG = results.best_checkpoint
print("Best checkpont:", best_checkpoint_DDPG)

estack` has been deprecated. Use `num_framestacks (int)` instead. This will raise an error in the future!
(pid=29734) /Users/matiascovarrubias/Library/Caches/pypoetry/virtualenvs/marketsai-reVLCGV_-py3.8/lib/python3.8/site-packages/ray/rllib/agents/ddpg/ddpg_torch_model.py:56: UserWarning: The given NumPy array is not writeable, and PyTorch does not support non-writeable tensors. This means you can write to the underlying (supposedly non-writeable) NumPy array using the tensor. You may want to copy the array to protect its data or make it writeable before converting it to a tensor. This type of warning will be suppressed for the rest of this program. (Triggered internally at  ../torch/csrc/utils/tensor_numpy.cpp:143.)
(pid=29734)   torch.from_numpy(self.action_space.low).float())
(pid=29734) 2021-04-12 15:03:42,221	WARNING deprecation.py:33 -- DeprecationWarning: `framestack` has been deprecated. Use `num_framestacks (int)` instead. This will raise an error in the future!
(pid=29735) 2

Result for DDPG_diffdemand_c893c_00000:
  custom_metrics: {}
  date: 2021-04-12_15-03-54
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 56.0930330727414
  episode_reward_mean: 51.491426373001325
  episode_reward_min: 44.109462260047835
  episodes_this_iter: 16
  episodes_total: 24
  experiment_id: 408a4ebda6c44550bef02b0dd09cf0b5
  hostname: Matiass-MacBook-Pro.local
  info:
    last_target_update_ts: 2504
    learner:
      policy_0:
        actor_loss: -0.46607890725135803
        allreduce_latency: 0.0
        critic_loss: 0.0005611776141449809
        max_q: 0.628998339176178
        mean_q: 0.476421058177948
        mean_td_error: 0.0019068008987233043
        min_q: 0.38785067200660706
        td_error: "[ 0.07837963 -0.05513912  0.16240585  0.0634346  -0.11637056  0.03621751\n\
          \  0.06167123  0.07347596  0.07226807  0.09271479 -0.06468573  0.07092172\n\
          \ -0.07754868  0.12444997 -0.13558644  0.13953602 -0.14107156 -0.00931734\n\
          \ -0.

Result for DDPG_diffdemand_c893c_00000:
  custom_metrics: {}
  date: 2021-04-12_15-04-04
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 56.0930330727414
  episode_reward_mean: 48.49166544485884
  episode_reward_min: 39.130900551074205
  episodes_this_iter: 8
  episodes_total: 32
  experiment_id: 408a4ebda6c44550bef02b0dd09cf0b5
  hostname: Matiass-MacBook-Pro.local
  info:
    last_target_update_ts: 3504
    learner:
      policy_0:
        actor_loss: -0.5081722736358643
        allreduce_latency: 0.0
        critic_loss: 0.0005460760439746082
        max_q: 0.7106596231460571
        mean_q: 0.5253397822380066
        mean_td_error: 0.0009158630855381489
        min_q: 0.39330145716667175
        td_error: "[ 0.10459054  0.04601893  0.03217191 -0.32544038  0.06285962 -0.04447824\n\
          \  0.02846029  0.14891553  0.10442525  0.02858546  0.06073084  0.02734905\n\
          \  0.05973822  0.02816656 -0.10992944  0.15510905 -0.29908168  0.0365299\n\
          \  0.02

Result for DDPG_diffdemand_c893c_00000:
  custom_metrics: {}
  date: 2021-04-12_15-04-15
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 56.0930330727414
  episode_reward_mean: 46.670727778385604
  episode_reward_min: 38.82628590346042
  episodes_this_iter: 8
  episodes_total: 40
  experiment_id: 408a4ebda6c44550bef02b0dd09cf0b5
  hostname: Matiass-MacBook-Pro.local
  info:
    last_target_update_ts: 4504
    learner:
      policy_0:
        actor_loss: -0.5261380672454834
        allreduce_latency: 0.0
        critic_loss: 0.0005984041490592062
        max_q: 0.7574036121368408
        mean_q: 0.5449230074882507
        mean_td_error: -0.008061928674578667
        min_q: 0.390208899974823
        td_error: "[ 0.01960599  0.12740499 -0.24688905  0.05520904  0.01828727  0.01614964\n\
          \ -0.13582867  0.01979306  0.02757034  0.11368519 -0.09061667  0.00877362\n\
          \ -0.20448297  0.02318186 -0.28860694  0.02053252  0.01614964 -0.17366433\n\
          \ -0.163

Result for DDPG_diffdemand_c893c_00000:
  custom_metrics: {}
  date: 2021-04-12_15-04-25
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 56.0930330727414
  episode_reward_mean: 45.476668357230466
  episode_reward_min: 38.82628590346042
  episodes_this_iter: 8
  episodes_total: 48
  experiment_id: 408a4ebda6c44550bef02b0dd09cf0b5
  hostname: Matiass-MacBook-Pro.local
  info:
    last_target_update_ts: 5504
    learner:
      policy_0:
        actor_loss: -0.6583638191223145
        allreduce_latency: 0.0
        critic_loss: 0.0006136372103355825
        max_q: 0.7849420309066772
        mean_q: 0.5911955237388611
        mean_td_error: -0.012876739725470543
        min_q: 0.3846973776817322
        td_error: "[-1.22592866e-01 -6.10178113e-02  5.46039939e-02  5.15798926e-02\n\
          \  4.34563756e-02 -2.27396488e-01 -7.97448754e-02 -9.39368606e-02\n -2.43647754e-01\
          \ -2.12333083e-01 -1.58310413e-01 -6.01067543e-02\n -2.26107001e-01  3.75545025e-03\
         

...

Result for DDPG_diffdemand_c893c_00000:
  custom_metrics: {}
  date: 2021-04-12_15-04-46
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 56.0930330727414
  episode_reward_mean: 42.50204271212579
  episode_reward_min: 35.93767996260311
  episodes_this_iter: 8
  episodes_total: 72
  experiment_id: 408a4ebda6c44550bef02b0dd09cf0b5
  hostname: Matiass-MacBook-Pro.local
  info:
    last_target_update_ts: 7504
    learner:
      policy_0:
        actor_loss: -0.7226266860961914
        allreduce_latency: 0.0
        critic_loss: 0.0004650880873668939
        max_q: 0.893939197063446
        mean_q: 0.6835399866104126
        mean_td_error: -0.00878012366592884
        min_q: 0.5265695452690125
        td_error: "[ 2.41695046e-02  1.03499293e-02 -1.82884574e-01 -2.31153667e-01\n\
          \  2.55886912e-02  2.59917378e-02  2.74375081e-02  1.91146493e-01\n  7.99137354e-03\
          \  2.04629898e-02  7.63852000e-02 -2.74757683e-01\n  2.32144594e-02  1.08035922e-01\
          \ 

Result for DDPG_diffdemand_c893c_00000:
  custom_metrics: {}
  date: 2021-04-12_15-04-57
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 56.0930330727414
  episode_reward_mean: 41.88335145121788
  episode_reward_min: 35.93767996260311
  episodes_this_iter: 8
  episodes_total: 80
  experiment_id: 408a4ebda6c44550bef02b0dd09cf0b5
  hostname: Matiass-MacBook-Pro.local
  info:
    last_target_update_ts: 8504
    learner:
      policy_0:
        actor_loss: -0.7600094079971313
        allreduce_latency: 0.0
        critic_loss: 0.00048240573960356414
        max_q: 0.9262548089027405
        mean_q: 0.7312755584716797
        mean_td_error: -0.01703658513724804
        min_q: 0.5787982940673828
        td_error: "[ 1.59913301e-02 -2.34491765e-01  1.68766379e-02  1.49891973e-02\n\
          \ -4.79642749e-02  7.18195438e-02  6.99090958e-03 -6.64472580e-04\n  1.46655440e-02\
          \ -1.07059479e-02  2.00505495e-01  1.69336200e-02\n -9.34713483e-02  1.07594132e-02\
          

Result for DDPG_diffdemand_c893c_00000:
  custom_metrics: {}
  date: 2021-04-12_15-05-09
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 56.0930330727414
  episode_reward_mean: 41.37042861042514
  episode_reward_min: 35.86383869784273
  episodes_this_iter: 8
  episodes_total: 88
  experiment_id: 408a4ebda6c44550bef02b0dd09cf0b5
  hostname: Matiass-MacBook-Pro.local
  info:
    last_target_update_ts: 9504
    learner:
      policy_0:
        actor_loss: -0.8396894335746765
        allreduce_latency: 0.0
        critic_loss: 0.00043896661372855306
        max_q: 0.9795256853103638
        mean_q: 0.7694618701934814
        mean_td_error: -0.013088141568005085
        min_q: 0.6282723546028137
        td_error: "[ 0.01002342 -0.01844865 -0.01597005  0.01163679 -0.17623198  0.00674921\n\
          \ -0.21035123  0.06300437  0.01787001  0.05029774  0.03065401 -0.16085374\n\
          \ -0.01783901  0.00966543  0.10703808 -0.22864491  0.09764826 -0.06599927\n\
          \  0.18

Result for DDPG_diffdemand_c893c_00000:
  custom_metrics: {}
  date: 2021-04-12_15-05-23
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 61.91441305833922
  episode_reward_mean: 42.23897485779679
  episode_reward_min: 35.86383869784273
  episodes_this_iter: 16
  episodes_total: 104
  experiment_id: 408a4ebda6c44550bef02b0dd09cf0b5
  hostname: Matiass-MacBook-Pro.local
  info:
    last_target_update_ts: 10504
    learner:
      policy_0:
        actor_loss: -0.9311899542808533
        allreduce_latency: 0.0
        critic_loss: 0.0004345330235082656
        max_q: 1.060697317123413
        mean_q: 0.860946774482727
        mean_td_error: -0.0033799023367464542
        min_q: 0.7040072083473206
        td_error: "[ 0.04939014  0.02821594 -0.02119529  0.01650542  0.00352967 -0.18112224\n\
          \ -0.09040523  0.00188905  0.01383454 -0.0991233   0.02420008  0.02302003\n\
          \  0.02154779  0.0264436   0.02608293  0.02650076  0.0358364  -0.11829305\n\
          \  0.

KeyboardInterrupt: 

In [ ]:
shutdown()